In [18]:
# libraries

import pandas as pd
import numpy as np
import bz2
pd.set_option('display.max_columns', None)
import statistics
import matplotlib.pyplot as plt
import seaborn as sns
import math
import pingouin as pg
import statsmodels.api as sm
import matplotlib as mpl
from scipy import stats
from distfit import distfit
import scikit_posthocs as sp
import datetime as dt

pd.options.display.float_format = '{:.2f}'.format

import warnings
warnings.filterwarnings('ignore')

plt.rcParams["image.cmap"] = "Pastel2"

import gower
import plotly.graph_objects as go
from sklearn_extra.cluster import KMedoids
from sklearn.neighbors import NearestNeighbors
from random import sample
from numpy.random import uniform
import numpy as np
from math import isnan
from sklearn.metrics import silhouette_score

from sklearn.metrics import davies_bouldin_score

from sklearn import metrics

from sklearn.metrics import calinski_harabasz_score
from clusteval import clusteval

from clusterval import Clusterval

from scipy.cluster.hierarchy import linkage
from scipy.cluster.hierarchy import dendrogram
from scipy.cluster.hierarchy import cut_tree

from sklearn.cluster import AgglomerativeClustering
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans,DBSCAN,MiniBatchKMeans
from matplotlib.colors import ListedColormap

from sklearn.cluster import DBSCAN

from scipy.spatial.distance import euclidean

from yellowbrick.regressor import PredictionError

import pygwalker as pyg

In [19]:
# importing data

df = pd.read_csv("/home/evida-monika/mhunters/final_data_3.csv.bz2", compression="bz2", sep=",")

# this is cleaned dataset
# we need to delete another user - ID = 235, because it has 274 sessions in 4 weeks - impossible.

df = df[df['id_users'] != 235]

In [20]:
# planting seed

import random

random.seed(10)

In [21]:
# changing types of data

cols = ['name_en_exercises','discarded_session_execution', 'code_name_sessions', 
        'name_en_sessions', 'active_user_programs', 'completed_user_programs',
        'pro_programs', 'available_programs', 'name_en_programs', 
        'gender', 
        'activity_level', 'goal', 'body_type', 'newsletter_subscription', 'notifications_setting',
        'language', 'scientific_data_usage', 'BMI_category', 'name_en_implements']

for col in cols:
    df[col] = df[col].astype('category')
    
col_date = ['updated_at_ex_ex', 'created_at_exercises', 'updated_at_exercises',
            'updated_at_session_execution', 'created_at_user_programs', 'updated_at_user_programs',
            'created_at_programs', 'updated_at_programs', 'created_at_users', 'updated_at_users',
            'date_of_birth']

for col in col_date:
    df[col] = pd.to_datetime(df[col])#.dt.strftime("%Y-%m-%d %H:%M:%S")

cat_names = {
    'gender': {1: 'male', 0: 'female'},
    'activity_level': {0: 'very active', 1: 'active', 2: 'sedentary'},
    'goal': {0: 'lose', 1: 'gain', 2: 'antiaging'},
    'body_type': {0: 'thin', 1: 'mid', 2: 'strong'}
}

df = df.replace(cat_names)


In [22]:
# dataset only for users

df_users_only_once = df.drop_duplicates(subset=['id_users'], keep='first')

In [23]:
# here dropping all of the columns that are not relevant for users

df_users_only = df_users_only_once.loc[:, ['id_users', 'created_at_users', 'updated_at_users', 'gender',
       'date_of_birth', 'height', 'weight', 'activity_level', 'goal',
       'body_type', 'body_fat', 'newsletter_subscription',
       'notifications_setting', 'training_days_setting', 'language', 'points',
       'scientific_data_usage', 'best_weekly_streak_users', 'BMI', 'BMI_category', 'total_sessions_users2',
                                          'total_time_users2', 'total_reps_users2', 'reps_per_session_users2',
                                          'total_calories_users2', 'kcal_per_session_users2']]

In [24]:
# dataset for only one of id_session_execution

df_session_exe_only_once = df.drop_duplicates(subset=['id_session_execution'], keep='first')

In [25]:
# here dropping all of the columns that are not relevant for session_execution

df_session_exe = df_session_exe_only_once.loc[:, ['id_session_execution', 
                                                  'difficulty_feedback_session_execution',
       'enjoyment_feedback_session_execution',
       'reps_executed_session_execution', 'updated_at_session_execution',
       'discarded_session_execution', 'id_sessions', 'order_sessions',
       'time_duration_sessions', 'code_name_sessions', 'name_en_sessions',
       'id_user_programs', 'created_at_user_programs',
       'updated_at_user_programs', 'active_user_programs',
       'current_session_id_user_programs', 'completed_user_programs',
       'id_programs', 'created_at_programs', 'updated_at_programs',
       'pro_programs', 'available_programs', 'strength_programs',
       'endurance_programs', 'technique_programs', 'flexibility_programs',
       'intensity_programs', 'name_en_programs', 'description_en_programs',
       'id_users', 'created_at_users', 'updated_at_users', 'gender',
       'date_of_birth', 'height', 'weight', 'activity_level', 'goal',
       'body_type', 'body_fat', 'newsletter_subscription',
       'notifications_setting', 'training_days_setting', 'language', 'points',
       'scientific_data_usage', 'best_weekly_streak_users', 'BMI', 'BMI_category', 'total_sessions_users2',
       'total_time_session_execution', 'total_reps_session_execution',
       'total_time_users2', 'total_reps_users2', 'reps_per_session_users2',
       'total_time_session_execution_min', 'reps_per_min_session_execution',
       'exercise_execution_time_min', 'calories_session_execution',
       'total_calories_users2', 'kcal_per_session_users2',
                                          'YYYY/WW']]

In [26]:
# manipulations

users_import = pd.read_csv("/home/evida-monika/mhunters/users.csv", sep=",")

users_import = users_import.loc[:, ['id', 'imported']]

users_import.replace('t', True, inplace = True)
users_import.replace('f', False, inplace = True)

# users_import_true = users_import[users_import['imported'] == True]

# imported_true = df_users_only_once.merge(users_import_true, how = 'inner', left_on = 'id_users', right_on = 'id')

users_import2 = users_import[users_import['imported'] == False]

# users_import.shape

imported = df_users_only_once.merge(users_import, how = 'inner', left_on = 'id_users', right_on = 'id')

# df_users_only.shape

imported.shape

imported_all = df.merge(users_import, how = 'inner', left_on = 'id_users', right_on = 'id')

df.shape

imported_all.shape

imported_sessions = df_session_exe.merge(users_import, how = 'inner', left_on = 'id_users', right_on = 'id')

df_session_exe.shape

imported_sessions.shape

imported_sessions = imported_sessions.sort_values(['id_users','updated_at_session_execution'])

imported_sessions_lat_sess = imported_sessions.drop_duplicates(subset=['id_users'], keep = 'last')

# imported_sessions_lat_sess[(imported_sessions_lat_sess['imported'] == True) & (imported_sessions_lat_sess['updated_at_session_execution'].dt.year == 2022)]

# imported_sessions_lat_sess[(imported_sessions_lat_sess['imported'] == True) & (imported_sessions_lat_sess['updated_at_session_execution'] > '2021-11-01')]

# imported_sessions_lat_sess[(imported_sessions_lat_sess['imported'] == True) & (imported_sessions_lat_sess['updated_at_session_execution'] > '2021-11-01') & (imported_sessions_lat_sess['updated_at_session_execution'].dt.year == 2021)]

imported_sessions_lat_sess_users = imported_sessions_lat_sess[(imported_sessions_lat_sess['updated_at_session_execution'] > '2021-11-01')]

imported_sessions_lat_sess_users = imported_sessions_lat_sess_users.loc[:, ['id_users']]

imported_sessions_lat_sess[(imported_sessions_lat_sess['updated_at_session_execution'] >= '2021-12-01')]['id_users']

df_after_upgrade = df.merge(imported_sessions_lat_sess_users, how = 'inner', left_on = 'id_users', right_on = 'id_users')

df_after_upgrade.shape # number of exercise executions after 1st deletion (1.11.2021)

df_session_after_upgrade = df_session_exe.merge(imported_sessions_lat_sess_users, how = 'inner', left_on = 'id_users', right_on = 'id_users')

df_session_after_upgrade.shape # number of sessions after 1st deletion (1.11.2021)

df_session_exe.shape

imported_sessions_lat_sess_users_other_date = imported_sessions_lat_sess[(imported_sessions_lat_sess['updated_at_session_execution'] >= '2021-12-01')]

df_after_upgrade_other_date = df.merge(imported_sessions_lat_sess_users_other_date, how = 'inner', left_on = 'id_users', right_on = 'id_users')

df_after_upgrade_other_date.shape # number of exercise executions after 2nd deletion (1.12.2021)

df_session_after_upgrade_other_date = df_session_exe.merge(imported_sessions_lat_sess_users_other_date, how = 'inner', left_on = 'id_users', right_on = 'id_users')

df_session_after_upgrade_other_date.shape # number of sessions after 2nd deletion (1.12.2021)


df_session_after_upgrade_users = df_session_after_upgrade.drop_duplicates(['id_users'], keep = 'last')

df_session_after_upgrade_users.shape # number of users after 1st deletion of data (1.11.2021)

df_after_upgrade_other_date_users = df_after_upgrade_other_date.drop_duplicates(['id_users'], keep = 'last')

df_after_upgrade_other_date_users.shape # number of users after 2nd deletion (1.12.2021)

# looking only for data without imported users
imported_only_false = imported_all[imported_all['imported'] == False]

imported_only_false = imported_only_false.sort_values(['id_users','updated_at_session_execution'])

imported_only_false_sess_exe = imported_only_false.drop_duplicates(['id_session_execution'], keep = 'last')

imported_only_false_sess_exe.shape # number of sessions after deleting all users that were in a new app

imported_only_false_users = imported_only_false.drop_duplicates(['id_users'], keep = 'last')

#imported_only_false_users.shape # number of users after deleting all users that were in a new app

In [28]:
# DFS CHANGES

# all
df = df_after_upgrade.copy()

# changing types of data

cols = ['name_en_exercises','discarded_session_execution', 'code_name_sessions', 
        'name_en_sessions', 'active_user_programs', 'completed_user_programs',
        'pro_programs', 'available_programs', 'name_en_programs', 
        'gender', 
        'activity_level', 'goal', 'body_type', 'newsletter_subscription', 'notifications_setting',
        'language', 'scientific_data_usage', 'BMI_category', 'name_en_implements']

for col in cols:
    df[col] = df[col].astype('category')
    
col_date = ['updated_at_ex_ex', 'created_at_exercises', 'updated_at_exercises',
            'updated_at_session_execution', 'created_at_user_programs', 'updated_at_user_programs',
            'created_at_programs', 'updated_at_programs', 'created_at_users', 'updated_at_users',
            'date_of_birth']

for col in col_date:
    df[col] = pd.to_datetime(df[col])#.dt.strftime("%Y-%m-%d %H:%M:%S")

cat_names = {
    'gender': {1: 'male', 0: 'female'},
    'activity_level': {0: 'very active', 1: 'active', 2: 'sedentary'},
    'goal': {0: 'lose', 1: 'gain', 2: 'antiaging'},
    'body_type': {0: 'thin', 1: 'mid', 2: 'strong'}
}

df = df.replace(cat_names)

exercise_per_sess = pd.DataFrame(df.groupby(['id_session_execution'])['id_session_execution'].count())

exercise_per_sess.rename(columns = {'id_session_execution': 'number_exercises_in_session'}, inplace = True)

exercise_per_sess.reset_index(inplace = True)

df_no_rest = df[df['name_en_exercises'] != 'Rest']

exercise_per_sess_no_rest = pd.DataFrame(df_no_rest.groupby(['id_session_execution'])['id_session_execution'].count())

exercise_per_sess_no_rest.rename(columns = {'id_session_execution': 'number_exercises_without_rest_in_session'}, inplace = True)

exercise_per_sess_no_rest.reset_index(inplace = True)

df = df.merge(exercise_per_sess, how = 'left', left_on = 'id_session_execution', right_on = 'id_session_execution')

df = df.merge(exercise_per_sess_no_rest, how = 'left', left_on = 'id_session_execution', right_on = 'id_session_execution')

'''
df.drop(['number_exercises_without_rest_in_session_y', 'number_exercises_in_session_y'], inplace = True, axis = 1)

df.rename(columns = {'number_exercises_without_rest_in_session_x': 'number_exercises_without_rest_in_session',
                     'number_exercises_in_session_x': 'number_exercises_in_session'},
         inplace = True)
'''


exercises_per_user = pd.DataFrame(df.groupby(['id_users'])['number_exercises_in_session'].sum())

exercises_per_user.rename(columns = {'number_exercises_in_session': 'exercises_per_user'}, inplace = True)

exercises_per_user.reset_index(inplace = True)

df = df.merge(exercises_per_user, how = 'left', left_on = 'id_users', right_on = 'id_users')

'''
df.drop(['exercises_per_user_y'], axis = 1, inplace = True)
df.rename(columns = {'exercises_per_user_x': 'exercises_per_users'},
         inplace = True)

'''

exercises_no_rest_per_user = pd.DataFrame(df.groupby(['id_users'])['number_exercises_without_rest_in_session'].sum())

exercises_no_rest_per_user.rename(columns = {'number_exercises_without_rest_in_session': 'exercises_without_rest_per_user'}, inplace = True)

exercises_no_rest_per_user.reset_index(inplace = True)

df = df.merge(exercises_no_rest_per_user, how = 'left', left_on = 'id_users', right_on = 'id_users')

'''
df.drop(['exercises_without_rest_per_user_y'], axis = 1, inplace = True)
df.rename(columns = {'exercises_without_rest_per_user_x': 'exercises_without_rest_per_users'},
         inplace = True)
'''

# users
df_users_only_once = df.drop_duplicates(subset=['id_users'], keep='first')

# here dropping all of the columns that are not relevant for users

df_users_only = df_users_only_once.loc[:, ['id_users', 'created_at_users', 'updated_at_users', 'gender',
       'date_of_birth', 'height', 'weight', 'activity_level', 'goal',
       'body_type', 'body_fat', 'newsletter_subscription',
       'notifications_setting', 'training_days_setting', 'language', 'points',
       'scientific_data_usage', 'best_weekly_streak_users', 'BMI', 'BMI_category', 'total_sessions_users2',
                                          'total_time_users2', 'total_reps_users2', 'reps_per_session_users2',
                                          'total_calories_users2', 'kcal_per_session_users2',
                                           'exercises_per_user', 'exercises_without_rest_per_user']]

# dataset for only one of id_session_execution

df_session_exe_only_once = df.drop_duplicates(subset=['id_session_execution'], keep='first')

# here dropping all of the columns that are not relevant for session_execution

df_session_exe = df_session_exe_only_once.loc[:, ['id_session_execution', 
                                                  'difficulty_feedback_session_execution',
       'enjoyment_feedback_session_execution',
       'reps_executed_session_execution', 'updated_at_session_execution',
       'discarded_session_execution', 'id_sessions', 'order_sessions',
       'time_duration_sessions', 'code_name_sessions', 'name_en_sessions',
       'id_user_programs', 'created_at_user_programs',
       'updated_at_user_programs', 'active_user_programs',
       'current_session_id_user_programs', 'completed_user_programs',
       'id_programs', 'created_at_programs', 'updated_at_programs',
       'pro_programs', 'available_programs', 'strength_programs',
       'endurance_programs', 'technique_programs', 'flexibility_programs',
       'intensity_programs', 'name_en_programs', 'description_en_programs',
       'id_users', 'created_at_users', 'updated_at_users', 'gender',
       'date_of_birth', 'height', 'weight', 'activity_level', 'goal',
       'body_type', 'body_fat', 'newsletter_subscription',
       'notifications_setting', 'training_days_setting', 'language', 'points',
       'scientific_data_usage', 'best_weekly_streak_users', 'BMI', 'BMI_category', 'total_sessions_users2',
       'total_time_session_execution', 'total_reps_session_execution',
       'total_time_users2', 'total_reps_users2', 'reps_per_session_users2',
       'total_time_session_execution_min', 'reps_per_min_session_execution',
       'exercise_execution_time_min', 'calories_session_execution',
       'total_calories_users2', 'kcal_per_session_users2',
                                          'YYYY/WW', 'number_exercises_in_session',
                                                 'number_exercises_without_rest_in_session']]

"\ndf.drop(['exercises_without_rest_per_user_y'], axis = 1, inplace = True)\ndf.rename(columns = {'exercises_without_rest_per_user_x': 'exercises_without_rest_per_users'},\n         inplace = True)\n"

In [33]:
# Creating a variable where there are 1 when it is the first time that user did a session in a day and 0 if the user already did a session that day

df_session_exe_copy = df_session_exe.copy()

df_session_exe_copy = df_session_exe_copy.sort_values(['id_users', 'updated_at_session_execution'])

df_session_exe_copy['days_a_week_session_exe'] = np.where((df_session_exe_copy['YYYY/WW'] == df_session_exe_copy['YYYY/WW'].shift()) &
                                                (df_session_exe_copy['updated_at_session_execution'].dt.year == df_session_exe_copy['updated_at_session_execution'].dt.year.shift()) &
                                                (df_session_exe_copy['updated_at_session_execution'].dt.month == df_session_exe_copy['updated_at_session_execution'].dt.month.shift()) &
                                                (df_session_exe_copy['updated_at_session_execution'].dt.day == df_session_exe_copy['updated_at_session_execution'].dt.day.shift()) & 
                                                (df_session_exe_copy['id_users'] == df_session_exe_copy['id_users'].shift()),
                                                0,1)


In [34]:
# grouped table with calculation of days trained a week for every user and training days setting by the user

df_session_exe_copy2 = df_session_exe_copy.loc[:, ['id_users', 'YYYY/WW', 'days_a_week_session_exe']]

df_session_exe_days_setting = df_session_exe_copy2.groupby(['id_users', 'YYYY/WW'])['days_a_week_session_exe'].sum().reset_index()


df_users_training_days_setting = df_users_only.loc[:, ['id_users', 'training_days_setting']]

df_session_exe_days_setting = df_session_exe_days_setting.merge(df_users_training_days_setting, how = 'left', 
                                                                left_on = 'id_users', right_on = 'id_users')


In [35]:
# new column that says if user achieved weekly training goal (1) or not (0)

df_session_exe_days_setting['training_days_setting'] = df_session_exe_days_setting['training_days_setting'].astype('int64')

df_session_exe_days_setting['training_days_goal_achieved'] = np.where(df_session_exe_days_setting['days_a_week_session_exe'] >= df_session_exe_days_setting['training_days_setting'], 1, 0)


In [38]:
pyg.walk(df_users_only)